In [33]:
import os
import pandas as pd

def remove_columns_from_csv(file_path):
    # Read the content of the CSV file
    data = pd.read_csv(file_path)

    # Drop the specified columns if they exist
    columns_to_drop = ['PER', 'TIME', 'OPENINT', 'HIGH', 'LOW']
    data.drop(columns=[col for col in columns_to_drop if col in data.columns], inplace=True)

    # Save the modified DataFrame back to the CSV file
    data.to_csv(file_path, index=False)

# Base directory where the folders with CSV files are located
base_dir = r'C:\Users\haziq\Downloads\d_us_txt\data\daily\us\nyse etfs'  # Replace this with your local directory path

# Iterate over all subdirectories and remove columns from CSV files
for subdir, dirs, files in os.walk(base_dir):
    for file in files:
        # Check if the file is a CSV file
        if file.endswith('.csv'):
            file_path = os.path.join(subdir, file)

            # Remove specified columns from the CSV file
            remove_columns_from_csv(file_path)

print("Columns removal completed!")



Columns removal completed!


In [41]:
import os
import pandas as pd

def add_value_column_and_drop_columns_from_csv(file_path):
    # Read the content of the CSV file
    data = pd.read_csv(file_path)

    # Create the 'VALUE' column as the average of 'OPEN' and 'CLOSE' columns, rounded to two decimal places
    data['VALUE'] = ((data['OPEN'] + data['CLOSE']) / 2).round(2)

    # Drop the 'OPEN' and 'CLOSE' columns
    data.drop(columns=['OPEN', 'CLOSE'], inplace=True)

    # Save the modified DataFrame back to the CSV file
    data.to_csv(file_path, index=False)

# Base directory where the folders with CSV files are located
base_dir = r'C:\Users\haziq\Downloads\d_us_txt\data\daily\us\nyse etfs'  # Replace this with your local directory path

# Iterate over all subdirectories and process CSV files
for subdir, dirs, files in os.walk(base_dir):
    for file in files:
        # Check if the file is a CSV file
        if file.endswith('.csv'):
            file_path = os.path.join(subdir, file)

            # Process the CSV file
            add_value_column_and_drop_columns_from_csv(file_path)

print("VALUE column added and OPEN & CLOSE columns dropped from all CSV files!")



VALUE column added and OPEN & CLOSE columns dropped from all CSV files!


In [48]:
#Remove .US from the ticker
import os
import pandas as pd

def remove_us_suffix_from_ticker(file_path):
    # Read the content of the CSV file
    data = pd.read_csv(file_path)

    # Remove the '.US' suffix from the 'TICKER' column, ensuring regex is set to False
    data['TICKER'] = data['TICKER'].str.replace('.US', '', regex=False)

    # Save the modified DataFrame back to the CSV file
    data.to_csv(file_path, index=False)

# Base directory where the folders with CSV files are located
base_dir = r'C:\Users\haziq\Downloads\d_us_txt\nyse etfs'  # Replace this with your local directory path

# Iterate over all subdirectories and process CSV files
for subdir, dirs, files in os.walk(base_dir):
    for file in files:
        # Check if the file is a CSV file
        if file.endswith('.csv'):
            file_path = os.path.join(subdir, file)

            # Remove '.US' suffix from the TICKER column in the CSV file
            remove_us_suffix_from_ticker(file_path)

print(".US suffix removed from TICKER column in all CSV files!")


.US suffix removed from TICKER column in all CSV files!


In [56]:
#change file name and add columns EXCHANGE and TYPE to the data
import os
import pandas as pd

def modify_csv_content_and_filename(file_path):
    # Read the content of the CSV file
    data = pd.read_csv(file_path)

    # Add 'EXCHANGE' and 'TYPE' columns with respective values
    data['EXCHANGE'] = 'NYSE'
    data['TYPE'] = 'ETF'

    # Construct the new filename without ".us"
    new_file_path = file_path.replace('.us.csv', '.nyse.etf.csv')

    # Save the modified DataFrame to the new CSV file
    data.to_csv(new_file_path, index=False)

    # Remove the original file if the filename was modified
    if new_file_path != file_path:
        os.remove(file_path)

# Base directory where the folders with CSV files are located
base_dir = r'C:\Users\haziq\Downloads\d_us_txt\nyse etfs'  # Replace this with your local directory path

# Iterate over all subdirectories and process CSV files
for subdir, dirs, files in os.walk(base_dir):
    for file in files:
        # Check if the file is a CSV file
        if file.endswith('.csv'):
            file_path = os.path.join(subdir, file)

            # Modify CSV content and filename
            modify_csv_content_and_filename(file_path)

print("Columns added and filenames modified for all CSV files!")


Columns added and filenames modified for all CSV files!


In [63]:
#Format Date
import os
import pandas as pd

def standardize_date_format(file_path):
    # Read the content of the CSV file
    data = pd.read_csv(file_path)

    sample_date = str(data['DATE'][0])

    # Check the format of the date
    if len(sample_date) == 8:  # If it's in YYYYMMDD format
        data['DATE'] = pd.to_datetime(data['DATE'], format='%Y%m%d').dt.strftime('%m/%Y/%d')
    elif "/" in sample_date:  # If it's already in MM/YYYY/DD format
        pass
    else:
        raise ValueError(f"Unknown date format in file: {file_path}")

    # Save the standardized DataFrame back to the CSV file
    data.to_csv(file_path, index=False)

# Base directory where the folders with CSV files are located
base_dir = r'C:\Users\haziq\Downloads\d_us_txt\Curated'  # Replace this with your local directory path

# Iterate over all subdirectories and process CSV files
for subdir, dirs, files in os.walk(base_dir):
    for file in files:
        # Check if the file is a CSV file
        if file.endswith('.csv'):
            file_path = os.path.join(subdir, file)

            # Standardize date format
            standardize_date_format(file_path)

print("Date format standardized for all CSV files!")



Date format standardized for all CSV files!


In [64]:
# calculate weekly average
import os
import pandas as pd

def convert_to_weekly(file_path):
    # Read the content of the CSV file
    data = pd.read_csv(file_path)

    # Convert the 'DATE' column to datetime format
    data['DATE'] = pd.to_datetime(data['DATE'], format='%m/%Y/%d')

    # Set the 'DATE' column as the index
    data.set_index('DATE', inplace=True)

    # Resample to get weekly data (with Wednesday as the anchor) and compute mean for 'VALUE'
    weekly_data = data.resample('W-WED').mean(numeric_only=True)

    # Forward fill the columns TICKER, VOL, EXCHANGE, and TYPE
    weekly_data[['TICKER', 'VOL', 'EXCHANGE', 'TYPE']] = data[['TICKER', 'VOL', 'EXCHANGE', 'TYPE']].resample('W-WED').ffill()

    # Reset the index
    weekly_data.reset_index(inplace=True)

    # Save the modified DataFrame back to the CSV file
    weekly_data.to_csv(file_path, index=False)

# Base directory where the folders with CSV files are located
base_dir = r'C:\Users\haziq\Downloads\d_us_txt\test'  # Replace this with your local directory path

# Iterate over all subdirectories and process CSV files
for subdir, dirs, files in os.walk(base_dir):
    for file in files:
        # Check if the file is a CSV file
        if file.endswith('.csv'):
            file_path = os.path.join(subdir, file)

            # Convert daily data to weekly data
            convert_to_weekly(file_path)

print("Data converted to weekly format for all CSV files!")


Data converted to weekly format for all CSV files!


In [75]:
#Convert to weekly average.
import pandas as pd
import os
import numpy as np
from datetime import datetime

# Define the path to the directory with your CSV files
directory_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated'  # Replace with the path to your directory

# Function to process each file
def process_stock_file(file_path):
    # Read the CSV file into a DataFrame
    df = pd.read_csv(file_path)

    # Convert the 'DATE' column to datetime
    df['DATE'] = pd.to_datetime(df['DATE'], format='%m/%Y/%d')

    # Generate a list of all Wednesdays within the range of the dates in the file
    start_date = df['DATE'].min()
    end_date = df['DATE'].max()
    wednesdays = pd.date_range(start=start_date, end=end_date, freq='W-WED')

    # Create a new column for the week number
    df['WEEK'] = df['DATE'].dt.isocalendar().week

    # Group by week and calculate the mean of 'VOL' and 'VALUE'
    weekly_means = df.groupby('WEEK')[['VOL', 'VALUE']].mean().reset_index()
    weekly_means['VOL'] = np.floor(weekly_means['VOL']).astype(int)



    # Create a DataFrame for Wednesdays
    wednesday_data = pd.DataFrame({'DATE': wednesdays})
    wednesday_data['WEEK'] = wednesday_data['DATE'].dt.isocalendar().week

    # Merge the weekly means with the Wednesday DataFrame
    wednesday_data = wednesday_data.merge(weekly_means, on='WEEK', how='left')

    # Drop the 'WEEK' column as it's no longer needed
    wednesday_data.drop('WEEK', axis=1, inplace=True)

    # Round the 'VOL' and 'VALUE' columns to two decimal places
    wednesday_data['VOL'] = wednesday_data['VOL'].round(2)
    wednesday_data['VALUE'] = wednesday_data['VALUE'].round(2)

    # Keep the 'TICKER', 'EXCHANGE', and 'TYPE' columns unchanged
    # We assume the first row has the correct values for these columns for all rows
    ticker = df['TICKER'].iloc[0]
    exchange = df['EXCHANGE'].iloc[0]
    stock_type = df['TYPE'].iloc[0]

    # Add these columns to the Wednesday DataFrame
    wednesday_data['TICKER'] = ticker
    wednesday_data['EXCHANGE'] = exchange
    wednesday_data['TYPE'] = stock_type

    # Reorder the columns to match the original file
    wednesday_data = wednesday_data[['TICKER', 'DATE', 'VOL', 'VALUE', 'EXCHANGE', 'TYPE']]

    # Convert 'DATE' back to the desired string format
    wednesday_data['DATE'] = wednesday_data['DATE'].dt.strftime('%m/%Y/%d')

    # Delete the original file
    os.remove(file_path)

    # Save the new DataFrame to a CSV file with the same filename
    wednesday_data.to_csv(file_path, index=False)

# Loop through each CSV file in the directory and process it
for filename in os.listdir(directory_path):
    if filename.endswith('.csv'):
        file_path = os.path.join(directory_path, filename)
        process_stock_file(file_path)



In [77]:
#replace type, exchange, with numbers.
import pandas as pd
import os

# Define your folder path here
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - numextype'

# Dictionary for replacements
type_replacements = {'STOCK': 0, 'ETF': 1}
exchange_replacements = {'NYSE': 0, 'NASDAQ': 1, 'NYSEMKT': 2}

# Loop through each file in the folder
for filename in os.listdir(folder_path):
    if filename.endswith('.csv'):
        # Construct the full file path
        file_path = os.path.join(folder_path, filename)

        # Read the CSV file
        df = pd.read_csv(file_path)

        # Replace 'TYPE' and 'EXCHANGE' values
        df['TYPE'] = df['TYPE'].map(type_replacements)
        df['EXCHANGE'] = df['EXCHANGE'].map(exchange_replacements)

        # Save the DataFrame back to CSV
        df.to_csv(file_path, index=False)

print("All files have been updated.")


All files have been updated.


In [6]:
#Delete Entries before 2017
import os
import pandas as pd

def process_csv(file_path):
    # Read the CSV file
    data = pd.read_csv(file_path)

    # Convert 'TICKER' to string
    data['TICKER'] = data['TICKER'].astype(str)

    # Convert 'DATE' to datetime format and filter for dates after 2014
    # The date format is 'MM/YYYY/DD'
    data['DATE'] = pd.to_datetime(data['DATE'], format='%m/%Y/%d', errors='coerce')
    data = data.dropna(subset=['DATE'])  # Drop rows where 'DATE' could not be converted
    data = data[data['DATE'].dt.year >= 2017]

    # Handle NaN values in 'VOL' before converting to integer
    # Option 1: Fill NaN values with 0 (or another placeholder value)
    data['VOL'] = data['VOL'].fillna(0).astype(int)
    # Option 2: Drop rows with NaN values in 'VOL'
    # data = data.dropna(subset=['VOL'])
    # data['VOL'] = data['VOL'].astype(int)

    # Format 'VALUE' to two decimal places
    data['VALUE'] = data['VALUE'].astype(float).round(2)

    # Remove rows with 'EXCHANGE' value 2 and convert to binary
    data = data[data['EXCHANGE'] != 2]
    data['EXCHANGE'] = data['EXCHANGE'].apply(lambda x: 1 if x == 1 else 0)

    # Convert 'DATE' back to string in the original format
    data['DATE'] = data['DATE'].dt.strftime('%m/%Y/%d')

    # No need to convert 'TYPE' as it is already binary

    # Save the modified DataFrame back to the original file
    data.to_csv(file_path, index=False)

# Replace with the path to your folder containing CSV files
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4'

# Process all CSV files in the folder
for filename in os.listdir(folder_path):
    if filename.endswith('.csv'):
        file_path = os.path.join(folder_path, filename)
        print(f'Processing file: {file_path}')
        process_csv(file_path)



Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\a.nyse.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aa.nyse.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aaa.nyse.etf.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aaau.nyse.etf.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aac-u.nyse.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aac-ws.nyse.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aac.nyse.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aacg.nasdaq.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aaci.nasdaq.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-4\aaciu.nasdaq.stock.csv
Processing file: C:\Users\haziq\Downloads\d_us_txt\Curated - after2015-

In [8]:
import os
import pandas as pd

def consolidate_csv(folder_path, output_file):
    # List to hold data from each CSV file
    all_data = []

    # Process all CSV files in the folder
    for filename in os.listdir(folder_path):
        if filename.endswith('.csv'):
            file_path = os.path.join(folder_path, filename)
            # Read the CSV file and append to the list
            all_data.append(pd.read_csv(file_path))

    # Concatenate all DataFrames into one
    combined_data = pd.concat(all_data, ignore_index=True)

    # Save the combined DataFrame into a new CSV file
    combined_data.to_csv(output_file, index=False)
    print(f"Consolidated file created at: {output_file}")

# Replace with the path to your folder containing CSV files and the desired output file path
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5'
output_file = r'C:\Users\haziq\Downloads\d_us_txt\consolidated_file.csv'

# Consolidate all CSV files into one
consolidate_csv(folder_path, output_file)


Consolidated file created at: C:\Users\haziq\Downloads\d_us_txt\consolidated_file.csv


In [13]:
import os

def convert_txt_to_csv(folder_path):
    for filename in os.listdir(folder_path):
        # Check for .txt files
        if filename.endswith('.txt'):
            # Define the old and new file paths
            old_file = os.path.join(folder_path, filename)
            new_file = os.path.join(folder_path, filename[:-4] + '.csv')

            # Rename the file
            os.rename(old_file, new_file)
            print(f"Renamed {old_file} to {new_file}")

# Replace with the path to your folder containing .txt files
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy'

# Convert all .txt files to .csv
convert_txt_to_csv(folder_path)


Renamed C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\a.us.txt to C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\a.us.csv
Renamed C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aa.us.txt to C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aa.us.csv
Renamed C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aaa.us.txt to C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aaa.us.csv
Renamed C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aaau.us.txt to C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aaau.us.csv
Renamed C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aac-u.us.txt to C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy\aac-u.us.csv
Renamed C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries

In [23]:
import os
import pandas as pd

def count_files_and_rows(folder_path):
    total_files = 0
    total_rows = 0

    # Process all files in the folder
    for root, dirs, files in os.walk(folder_path):
        for filename in files:
            if filename.endswith('.csv'):
                total_files += 1
                file_path = os.path.join(root, filename)
                # Read the CSV file and count the rows
                data = pd.read_csv(file_path)
                total_rows += len(data)

    return total_files, total_rows

# Replace with the path to your folder containing CSV files
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - after2017less 6years data9 - Copy'

# Get counts
total_files, total_rows = count_files_and_rows(folder_path)
print(f"Total number of CSV files: {total_files}")
print(f"Total number of rows across all CSV files: {total_rows}")

Total number of CSV files: 3902
Total number of rows across all CSV files: 1385685


In [25]:
import pandas as pd

# Replace with the path to your specific CSV file
file_path = r"C:\Users\haziq\Downloads\d_us_txt\consolidated_file.csv"

# Read the CSV file
data = pd.read_csv(file_path)

# Get the number of rows
num_rows = len(data)

print(f"The file {file_path} contains {num_rows} rows.")


The file C:\Users\haziq\Downloads\d_us_txt\consolidated_file.csv contains 2608650 rows.


In [14]:
import os
import pandas as pd

def delete_files_with_insufficient_data(folder_path):
    for filename in os.listdir(folder_path):
        if filename.endswith('.csv'):
            file_path = os.path.join(folder_path, filename)
            try:
                data = pd.read_csv(file_path)

                # Ensure 'DATE' is in datetime format
                data['DATE'] = pd.to_datetime(data['DATE'], errors='coerce')
                data.dropna(subset=['DATE'], inplace=True)

                # Calculate the number of unique years
                unique_years = data['DATE'].dt.year.nunique()

                if unique_years < 3:
                    os.remove(file_path)
                    print(f"Deleted {filename}: contains less than 3 years of data.")
                else:
                    print(f"Kept {filename}: meets the data requirement.")
            except Exception as e:
                print(f"Error processing {filename}: {e}")

# Replace with the path to your folder containing CSV files
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - after2017DeletedEntries5 - Copy'

# Execute the function
delete_files_with_insufficient_data(folder_path)



Deleted a.nyse.stock.csv: contains less than 3 years of data.
Deleted aa.nyse.stock.csv: contains less than 3 years of data.
Deleted aaa.nyse.etf.csv: contains less than 3 years of data.
Deleted aaau.nyse.etf.csv: contains less than 3 years of data.
Deleted aac-u.nyse.stock.csv: contains less than 3 years of data.
Deleted aac-ws.nyse.stock.csv: contains less than 3 years of data.
Deleted aac.nyse.stock.csv: contains less than 3 years of data.
Deleted aacg.nasdaq.stock.csv: contains less than 3 years of data.
Deleted aaci.nasdaq.stock.csv: contains less than 3 years of data.
Deleted aaciu.nasdaq.stock.csv: contains less than 3 years of data.
Deleted aaciw.nasdaq.stock.csv: contains less than 3 years of data.
Deleted aadi.nasdaq.stock.csv: contains less than 3 years of data.
Deleted aadr.nasdaq.etf.csv: contains less than 3 years of data.
Deleted aaic.nyse.stock.csv: contains less than 3 years of data.
Deleted aaic_b.nyse.stock.csv: contains less than 3 years of data.
Deleted aaic_c.nyse

In [22]:
import os
import pandas as pd

def delete_rows_in_small_files(folder_path):
    for filename in os.listdir(folder_path):
        if filename.endswith('.csv'):
            file_path = os.path.join(folder_path, filename)
            try:
                data = pd.read_csv(file_path)
                if len(data) < 310:
                    # Clear the DataFrame if row count is less than 145
                    data = pd.DataFrame()
                    # Save the emptied DataFrame back to the CSV, overwriting it
                    data.to_csv(file_path, index=False)
                    print(f"Cleared all data from {filename} because it had less than 310 rows.")
                else:
                    print(f"{filename} has sufficient rows and was not modified.")
            except Exception as e:
                print(f"Error processing {filename}: {e}")

# Replace with the path to your folder containing CSV files
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - after2017less 5 years data8 - Copy'

# Execute the function
delete_rows_in_small_files(folder_path)


a.nyse.stock.csv has sufficient rows and was not modified.
aa.nyse.stock.csv has sufficient rows and was not modified.
aacg.nasdaq.stock.csv has sufficient rows and was not modified.
Cleared all data from aadi.nasdaq.stock.csv because it had less than 310 rows.
aaic.nyse.stock.csv has sufficient rows and was not modified.
aal.nasdaq.stock.csv has sufficient rows and was not modified.
aame.nasdaq.stock.csv has sufficient rows and was not modified.
aaoi.nasdaq.stock.csv has sufficient rows and was not modified.
aaon.nasdaq.stock.csv has sufficient rows and was not modified.
aap.nyse.stock.csv has sufficient rows and was not modified.
aapl.nasdaq.stock.csv has sufficient rows and was not modified.
aat.nyse.stock.csv has sufficient rows and was not modified.
ab.nyse.stock.csv has sufficient rows and was not modified.
abbv.nyse.stock.csv has sufficient rows and was not modified.
abcb.nasdaq.stock.csv has sufficient rows and was not modified.
abeo.nasdaq.stock.csv has sufficient rows and was

In [26]:
import os
import pandas as pd

def consolidate_csv_files(folder_path, output_file):
    all_data = []

    # Traverse the folder and read each CSV file
    for filename in os.listdir(folder_path):
        if filename.endswith('.csv'):
            file_path = os.path.join(folder_path, filename)
            all_data.append(pd.read_csv(file_path))

    # Concatenate all data into a single DataFrame
    consolidated_data = pd.concat(all_data, ignore_index=True)

    # Save the consolidated data to a new CSV file without removing duplicates
    consolidated_data.to_csv(output_file, index=False)
    print(f"Consolidated file saved to {output_file}")

    # Count the total number of rows before removing duplicates
    total_rows_before = len(consolidated_data)
    print(f"Total number of rows before removing duplicates: {total_rows_before}")

    # Remove duplicate rows
    consolidated_data_no_duplicates = consolidated_data.drop_duplicates()

    # Save the consolidated data to a new CSV file after removing duplicates
    consolidated_no_dup_file = output_file.replace('.csv', '_no_duplicates.csv')
    consolidated_data_no_duplicates.to_csv(consolidated_no_dup_file, index=False)
    print(f"Consolidated file without duplicates saved to {consolidated_no_dup_file}")

    # Count the total number of rows after removing duplicates
    total_rows_after = len(consolidated_data_no_duplicates)
    print(f"Total number of rows after removing duplicates: {total_rows_after}")
    print(f"Number of duplicate rows removed: {total_rows_before - total_rows_after}")

# Replace with the path to your folder containing CSV files and the desired output file path
folder_path = r'C:\Users\haziq\Downloads\d_us_txt\Curated - after2017less 6years data9 - Copy'
output_file = r'C:\Users\haziq\Downloads\d_us_txt\consolidated_data.csv'

# Create a consolidated CSV file and check for duplicates
consolidate_csv_files(folder_path, output_file)


Consolidated file saved to C:\Users\haziq\Downloads\d_us_txt\consolidated_data.csv
Total number of rows before removing duplicates: 1385685
Consolidated file without duplicates saved to C:\Users\haziq\Downloads\d_us_txt\consolidated_data_no_duplicates.csv
Total number of rows after removing duplicates: 1385685
Number of duplicate rows removed: 0


In [28]:
import pandas as pd

# Path to your CSV file
csv_file_path = r"C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1.csv"

# Read the CSV file into a DataFrame
data = pd.read_csv(csv_file_path)

# Filter out rows where 'TYPE' column is 1
data_filtered = data[data['TYPE'] != 1]

# Save the filtered data back to CSV, overwriting the original file
# If you want to keep the original file unchanged, specify a different file name for the output
data_filtered.to_csv(csv_file_path, index=False)

print(f"Rows where 'TYPE' was 1 have been removed and the file has been overwritten at {csv_file_path}.")


Rows where 'TYPE' was 1 have been removed and the file has been overwritten at C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1.csv.


In [29]:
import pandas as pd

# Path to your CSV file
csv_file_path = r"C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1.csv"

# Read the CSV file into a DataFrame
data = pd.read_csv(csv_file_path)

# Print the number of rows before filtering
print(f"Number of rows before filtering: {len(data)}")

# Check how many rows have 'TYPE' as 1 before filtering
print(f"Rows with 'TYPE' == 1 before filtering: {sum(data['TYPE'] == 1)}")

# Filter out rows where 'TYPE' column is 1
data_filtered = data[data['TYPE'] != 1]

# Print the number of rows after filtering
print(f"Number of rows after filtering: {len(data_filtered)}")

# Save the filtered data back to CSV, overwriting the original file
data_filtered.to_csv(csv_file_path, index=False)

print(f"Rows where 'TYPE' was 1 have been removed and the file has been overwritten at {csv_file_path}.")


Number of rows before filtering: 1385685
Rows with 'TYPE' == 1 before filtering: 0
Number of rows after filtering: 1385685
Rows where 'TYPE' was 1 have been removed and the file has been overwritten at C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1.csv.


In [30]:
import pandas as pd

# Path to your CSV file
csv_file_path = 'C:\\Users\\haziq\\Downloads\\d_us_txt\\consolidated_data_1.csv'

# Read the CSV file into a DataFrame
data = pd.read_csv(csv_file_path)

# Check the data type of the 'TYPE' column
print(f"Data type of 'TYPE' column: {data['TYPE'].dtype}")

# Check unique values in the 'TYPE' column
print(f"Unique values in 'TYPE' column: {data['TYPE'].unique()}")

# Check for any leading/trailing whitespace in column names
print(f"Column names with whitespace stripped: {[col.strip() for col in data.columns]}")

# Assuming 'TYPE' column is of the correct data type and name
# Filter out rows where 'TYPE' column is 1
data_filtered = data[data['TYPE'] != 1]
# Print the number of rows after filtering
print(f"Number of rows after filtering: {len(data_filtered)}")

# Save the filtered data back to CSV, overwriting the original file
data_filtered.to_csv(csv_file_path, index=False)

print(f"Rows where 'TYPE' was 1 have been removed and the file has been overwritten at {csv_file_path}.")
# Continue with the rest of the script...


Data type of 'TYPE' column: int64
Unique values in 'TYPE' column: [0]
Column names with whitespace stripped: ['TICKER', 'DATE', 'VOL', 'VALUE', 'EXCHANGE', 'TYPE']
Number of rows after filtering: 1385685
Rows where 'TYPE' was 1 have been removed and the file has been overwritten at C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1.csv.


In [31]:
import pandas as pd

# Path to your CSV file
csv_file_path = r"C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1 - Copy - Copy.csv"

# Read the CSV file into a DataFrame
data = pd.read_csv(csv_file_path)

# Drop the 'TYPE' column from the DataFrame
data = data.drop('TYPE', axis=1)

# Save the modified DataFrame back to CSV, overwriting the original file
data.to_csv(csv_file_path, index=False)

print(f"The 'TYPE' column has been removed and the file has been overwritten at {csv_file_path}.")


The 'TYPE' column has been removed and the file has been overwritten at C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1.csv.


In [37]:
import pandas as pd

# Replace with the actual path to your CSV file
csv_file_path = r"C:\Users\haziq\Downloads\d_us_txt\consolidated_without type-2 - Copy.csv"

# Read the CSV file into a DataFrame
data = pd.read_csv(csv_file_path)

# Convert the 'DATE' column to datetime
data['DATE'] = pd.to_datetime(data['DATE'], format='%m/%Y/%d')

# Drop rows where 'EXCHANGE' column is 1
data = data[data['EXCHANGE'] != 1]

# Drop the 'EXCHANGE' column from the DataFrame
data.drop('EXCHANGE', axis=1, inplace=True)

# Convert 'DATE' column back to string in the desired format
data['DATE'] = data['DATE'].dt.strftime('%m/%Y/%d')

# Save the modified DataFrame back to CSV, overwriting the original file
data.to_csv(csv_file_path, index=False)

print(f"Rows where 'EXCHANGE' was 1 have been removed, the 'EXCHANGE' column has been dropped, and the file has been overwritten with dates in the format 'MM/YYYY/DD' at {csv_file_path}.")


Rows where 'EXCHANGE' was 1 have been removed, the 'EXCHANGE' column has been dropped, and the file has been overwritten with dates in the format 'MM/YYYY/DD' at C:\Users\haziq\Downloads\d_us_txt\consolidated_without type-2 - Copy.csv.


In [33]:
import pandas as pd

# Path to your CSV file
csv_file_path = r'C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1 - Copy - Copy.csv'

# Read the CSV file into a DataFrame
data = pd.read_csv(csv_file_path)

# Drop the 'EXCHANGE' column from the DataFrame
data.drop('EXCHANGE', axis=1, inplace=True)

# Save the modified DataFrame back to CSV, overwriting the original file
data.to_csv(csv_file_path, index=False)

print(f"The 'EXCHANGE' column has been removed and the file has been overwritten at {csv_file_path}.")


The 'EXCHANGE' column has been removed and the file has been overwritten at C:\Users\haziq\Downloads\d_us_txt\consolidated_data_1 - Copy - Copy.csv.
